### Step 1 :  Installing & importing dependencies

In [3]:
!pip install torch torchvision torchaudio

In [10]:
!pip install transformers requests beautifulsoup4 numpy pandas 

  Using cached transformers-4.47.1-py3-none-any.whl (10.1 MB)
     -------------------------------------- 286.1/286.1 kB 2.0 MB/s eta 0:00:00
     -------------------------------------- 450.5/450.5 kB 1.8 MB/s eta 0:00:00
     ---------------------------------------- 2.4/2.4 MB 1.6 MB/s eta 0:00:00
     -------------------------------------- 183.9/183.9 kB 1.1 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2022.7.1
    Uninstalling fsspec-2022.7.1:
      Successfully uninstalled fsspec-2022.7.1


In [4]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch
import requests
from bs4 import BeautifulSoup
import re

import pandas as pd
import numpy as np

###  Step 2 : Instantiate Model

In [5]:
tokenizer = AutoTokenizer.from_pretrained('nlptown/bert-base-multilingual-uncased-sentiment')

tokenizer_config.json:   0%|          | 0.00/39.0 [00:00<?, ?B/s]

C:\Users\aditi\anaconda3\lib\site-packages\huggingface_hub\file_download.py:140: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\aditi\.cache\huggingface\hub\models--nlptown--bert-base-multilingual-uncased-sentiment. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


config.json:   0%|          | 0.00/953 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/872k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

In [6]:
model = AutoModelForSequenceClassification.from_pretrained('nlptown/bert-base-multilingual-uncased-sentiment')

model.safetensors:   0%|          | 0.00/669M [00:00<?, ?B/s]

### Step 3 : Encode & Calculate Sentiment 

In [7]:
# some reviews :
review1 = 'Hated this, the worst!'                # 1 star
review2 = 'Loved it!'                             # 5 stars
review3 = 'Eh, couldve been better'               # 3 stars

In [8]:
tokens = tokenizer.encode(review2, return_tensors = 'pt')

In [9]:
tokens

tensor([[  101, 46747, 10197,   106,   102]])

In [10]:
tokenizer.decode(tokens[0])      # trying out if the tokens are correctly decoded

'[CLS] loved it! [SEP]'

In [11]:
result = model(tokens)

In [12]:
result  # or  print(result) 

SequenceClassifierOutput(loss=None, logits=tensor([[-2.3504, -2.3835, -0.4771,  1.5117,  2.9500]],
       grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

In [13]:
result.logits

tensor([[-2.3504, -2.3835, -0.4771,  1.5117,  2.9500]],
       grad_fn=<AddmmBackward0>)

In [14]:
torch.argmax(result.logits)

tensor(4)

In [15]:
stars = int(torch.argmax(result.logits)) + 1
stars

5

### Step 4 : Collecting Data - i.e. Reviews

In [16]:
r = requests.get('https://www.yelp.com/biz/dumpling-kitchen-san-francisco-5')
r

<Response [200]>

In [17]:
r.text

'<!DOCTYPE html><html lang="en-US" prefix="og: http://ogp.me/ns#" style="margin: 0;padding: 0; border: 0; font-size: 100%; font: inherit; vertical-align: baseline;"><head><script>document.documentElement.className=document.documentElement.className.replace(/\x08no-js\x08/,"js");</script><meta http-equiv="Content-Type" content="text/html; charset=UTF-8" /><meta http-equiv="Content-Language" content="en-US" /><meta name="viewport" content="width=device-width, initial-scale=1, shrink-to-fit=no"><link rel="mask-icon" sizes="any" href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/b2bb2fb0ec9c/assets/img/logos/yelp_burst.svg" content="#FF1A1A"><link rel="shortcut icon" href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/dcfe403147fc/assets/img/logos/favicon.ico"><script> window.ga=window.ga||function(){(ga.q=ga.q||[]).push(arguments)};ga.l=+new Date;window.ygaPageStartTime=new Date().getTime();</script><script>\n            window.yelp = window.yelp || {};\

In [18]:
soup = BeautifulSoup(r.text,'html.parser')
soup

<!DOCTYPE html>
<html lang="en-US" prefix="og: http://ogp.me/ns#" style="margin: 0;padding: 0; border: 0; font-size: 100%; font: inherit; vertical-align: baseline;"><head><script>document.documentElement.className=document.documentElement.className.replace(/no-js/,"js");</script><meta content="text/html; charset=utf-8" http-equiv="Content-Type"/><meta content="en-US" http-equiv="Content-Language"/><meta content="width=device-width, initial-scale=1, shrink-to-fit=no" name="viewport"/><link content="#FF1A1A" href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/b2bb2fb0ec9c/assets/img/logos/yelp_burst.svg" rel="mask-icon" sizes="any"/><link href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/dcfe403147fc/assets/img/logos/favicon.ico" rel="shortcut icon"/><script> window.ga=window.ga||function(){(ga.q=ga.q||[]).push(arguments)};ga.l=+new Date;window.ygaPageStartTime=new Date().getTime();</script><script>
            window.yelp = window.yelp || {};
      

In [19]:
regex = re.compile('.*comment.*')
regex

re.compile(r'.*comment.*', re.UNICODE)

In [20]:
results = soup.find_all('p', {'class' : regex})

In [21]:
results

[<p class="comment__09f24__D0cxf y-css-1wfz87z"><span class="raw__09f24__T4Ezm" lang="en">My brother took me to this place while visiting San Francisco. We went right when it opened for the evening dinner rush and was seated right away.<br/><br/>The place is very small, but cozy and clean. Their bathroom was super clean and easy to find. The staff was friendly and explained dishes to us that were in Chinese on the menu. <br/><br/>We ordered the soup, dumplings, steamed dumplings, and the sizzling rice soup. We also ordered a scallion pancake. <br/><br/>The food came out at different times, which is very typical in this type of restaurant. We got the scallion pancake and the soup right away. Both were delicious! <br/><br/>The sizzling rice soup is made with a clear chicken broth and has some vegetables. The main ingredients are chicken, pork, shrimp, and the sizzling rice.  When the rice arrived to the table it was popping... And when it is dropped into the soup, it sizzles hence the na

In [22]:
results[0]

<p class="comment__09f24__D0cxf y-css-1wfz87z"><span class="raw__09f24__T4Ezm" lang="en">My brother took me to this place while visiting San Francisco. We went right when it opened for the evening dinner rush and was seated right away.<br/><br/>The place is very small, but cozy and clean. Their bathroom was super clean and easy to find. The staff was friendly and explained dishes to us that were in Chinese on the menu. <br/><br/>We ordered the soup, dumplings, steamed dumplings, and the sizzling rice soup. We also ordered a scallion pancake. <br/><br/>The food came out at different times, which is very typical in this type of restaurant. We got the scallion pancake and the soup right away. Both were delicious! <br/><br/>The sizzling rice soup is made with a clear chicken broth and has some vegetables. The main ingredients are chicken, pork, shrimp, and the sizzling rice.  When the rice arrived to the table it was popping... And when it is dropped into the soup, it sizzles hence the nam

In [23]:
results[0].text  #removes all the tags - only text remains

"My brother took me to this place while visiting San Francisco. We went right when it opened for the evening dinner rush and was seated right away.The place is very small, but cozy and clean. Their bathroom was super clean and easy to find. The staff was friendly and explained dishes to us that were in Chinese on the menu. We ordered the soup, dumplings, steamed dumplings, and the sizzling rice soup. We also ordered a scallion pancake. The food came out at different times, which is very typical in this type of restaurant. We got the scallion pancake and the soup right away. Both were delicious! The sizzling rice soup is made with a clear chicken broth and has some vegetables. The main ingredients are chicken, pork, shrimp, and the sizzling rice.  When the rice arrived to the table it was popping... And when it is dropped into the soup, it sizzles hence the name.The dumplings were very tasty. And they were a good size. The pork dumplings are very hot when they come out so you need to be

In [24]:
# converting all of it into text reviews 
reviews = [i.text for i in results]

In [25]:
reviews

["My brother took me to this place while visiting San Francisco. We went right when it opened for the evening dinner rush and was seated right away.The place is very small, but cozy and clean. Their bathroom was super clean and easy to find. The staff was friendly and explained dishes to us that were in Chinese on the menu. We ordered the soup, dumplings, steamed dumplings, and the sizzling rice soup. We also ordered a scallion pancake. The food came out at different times, which is very typical in this type of restaurant. We got the scallion pancake and the soup right away. Both were delicious! The sizzling rice soup is made with a clear chicken broth and has some vegetables. The main ingredients are chicken, pork, shrimp, and the sizzling rice.  When the rice arrived to the table it was popping... And when it is dropped into the soup, it sizzles hence the name.The dumplings were very tasty. And they were a good size. The pork dumplings are very hot when they come out so you need to b

### Step 5 : Load Reviews into the DataFrame & Score

In [26]:
df = pd.DataFrame(np.array(reviews), columns=['reviews'])

In [27]:
df.head()

reviews
0  My brother took me to this place while visitin...
1  Always a solid and delicious spot, this place ...
2  Dear Helena,  Thank you for your kind words an...
3  Dumpling kitchen has been a family favorite fo...
4  Dear Emily, Thank you for your honest feedback...

In [28]:
df.tail()

reviews
12  Dear Rose, we're truly grateful for your posit...
13  This came up when I searched "cheap eats" in t...
14  Came here for a late lunch and got:-Shanghai s...
15  We stopped here shortly after they opened. The...
16  Dear Christina, Thank you for visiting us! We'...

In [29]:
df

reviews
0   My brother took me to this place while visitin...
1   Always a solid and delicious spot, this place ...
2   Dear Helena,  Thank you for your kind words an...
3   Dumpling kitchen has been a family favorite fo...
4   Dear Emily, Thank you for your honest feedback...
5   Unfortunately a little disappointed by the ite...
6   Dear Evelynne, thank you for taking the time t...
7   Dumpling kitchen has some gluten free items on...
8   Dear Dina, We're glad to hear you found some g...
9   3.5 stars. New dumpling place!Service is amazi...
10  Dear Sammi, Thank you for your feedback and fo...
11  So delicious and felt very homey! For 3 people...
12  Dear Rose, we're truly grateful for your posit...
13  This came up when I searched "cheap eats" in t...
14  Came here for a late lunch and got:-Shanghai s...
15  We stopped here shortly after they opened. The...
16  Dear Christina, Thank you for visiting us! We'...

In [46]:
df = df[~df['reviews'].str.contains("Dear", na=False)]     # to remove responses by owner
df = df.reset_index(drop=True)

In [47]:
df

reviews
0  My brother took me to this place while visitin...
1  Always a solid and delicious spot, this place ...
2  Dumpling kitchen has been a family favorite fo...
3  Unfortunately a little disappointed by the ite...
4  Dumpling kitchen has some gluten free items on...
5  3.5 stars. New dumpling place!Service is amazi...
6  So delicious and felt very homey! For 3 people...
7  This came up when I searched "cheap eats" in t...
8  Came here for a late lunch and got:-Shanghai s...
9  We stopped here shortly after they opened. The...

In [48]:
df['reviews']

0    My brother took me to this place while visitin...
1    Always a solid and delicious spot, this place ...
2    Dumpling kitchen has been a family favorite fo...
3    Unfortunately a little disappointed by the ite...
4    Dumpling kitchen has some gluten free items on...
5    3.5 stars. New dumpling place!Service is amazi...
6    So delicious and felt very homey! For 3 people...
7    This came up when I searched "cheap eats" in t...
8    Came here for a late lunch and got:-Shanghai s...
9    We stopped here shortly after they opened. The...
Name: reviews, dtype: object

In [49]:
df['reviews'][0]

"My brother took me to this place while visiting San Francisco. We went right when it opened for the evening dinner rush and was seated right away.The place is very small, but cozy and clean. Their bathroom was super clean and easy to find. The staff was friendly and explained dishes to us that were in Chinese on the menu. We ordered the soup, dumplings, steamed dumplings, and the sizzling rice soup. We also ordered a scallion pancake. The food came out at different times, which is very typical in this type of restaurant. We got the scallion pancake and the soup right away. Both were delicious! The sizzling rice soup is made with a clear chicken broth and has some vegetables. The main ingredients are chicken, pork, shrimp, and the sizzling rice.  When the rice arrived to the table it was popping... And when it is dropped into the soup, it sizzles hence the name.The dumplings were very tasty. And they were a good size. The pork dumplings are very hot when they come out so you need to be

In [50]:
def calc_sentiment_analysis_score(review):
    tokens = tokenizer.encode(review, return_tensors = 'pt')
    result = model(tokens)
    stars = int(torch.argmax(result.logits)) + 1
    return stars

In [51]:
calc_sentiment_analysis_score(df['reviews'][0])

5

In [53]:
df['reviews'][3]

"Unfortunately a little disappointed by the items my friends I ordered for dinner here. We were in the area after our soulcycle class and was craving Chinese food so we popped in here and was seated right away. We ordered the mapo tofu, sizzling rice soup, pan fried pork buns, and wontons in chili oil. The mapo tofu was pretty good, it had the sichuan peppercorn numbing taste and the tofu was soft and silky, I just wish it had a little bit more meat in it. The sizzling rice soup was very tasty and probably my favorite dish of the night. The two dumpling dishes felt a bit lackluster than my expectations (since this place is called dumpling kitchen). The pan fried pork buns weren't bad, but I felt it wasn't as crunchy on the bottom as it could've been. The meat inside was good though. The wontons in chili oil were not good, the chili oil had no spice to it, it was a very pale orange, it didn't feel like true chili oil. The wonton skins were also really thick in my opinion."

In [54]:
calc_sentiment_analysis_score(df['reviews'][3])

3

In [55]:
df

reviews
0  My brother took me to this place while visitin...
1  Always a solid and delicious spot, this place ...
2  Dumpling kitchen has been a family favorite fo...
3  Unfortunately a little disappointed by the ite...
4  Dumpling kitchen has some gluten free items on...
5  3.5 stars. New dumpling place!Service is amazi...
6  So delicious and felt very homey! For 3 people...
7  This came up when I searched "cheap eats" in t...
8  Came here for a late lunch and got:-Shanghai s...
9  We stopped here shortly after they opened. The...

In [56]:
df['sentiment analysis'] = df['reviews'].apply(lambda x: calc_sentiment_analysis_score(x[:512])) 
# the nlp pipeline is limited to processing only 512 tokens at a time 

In [57]:
df

reviews  sentiment analysis
0  My brother took me to this place while visitin...                   5
1  Always a solid and delicious spot, this place ...                   4
2  Dumpling kitchen has been a family favorite fo...                   4
3  Unfortunately a little disappointed by the ite...                   3
4  Dumpling kitchen has some gluten free items on...                   3
5  3.5 stars. New dumpling place!Service is amazi...                   3
6  So delicious and felt very homey! For 3 people...                   5
7  This came up when I searched "cheap eats" in t...                   5
8  Came here for a late lunch and got:-Shanghai s...                   4
9  We stopped here shortly after they opened. The...                   5

In [ ]:
# On checking manually, we see that out of 9 predicted values : 7 are correct and 2 are slightly off 

In [ ]:
# Trying this for a Spa Place review on Yelp

In [85]:
r = requests.get('https://www.yelp.com/biz/mysa-day-spa-san-francisco')
r

<Response [200]>

In [86]:
r.text

'<!DOCTYPE html><html lang="en-US" prefix="og: http://ogp.me/ns#" style="margin: 0;padding: 0; border: 0; font-size: 100%; font: inherit; vertical-align: baseline;"><head><script>document.documentElement.className=document.documentElement.className.replace(/\x08no-js\x08/,"js");</script><meta http-equiv="Content-Type" content="text/html; charset=UTF-8" /><meta http-equiv="Content-Language" content="en-US" /><meta name="viewport" content="width=device-width, initial-scale=1, shrink-to-fit=no"><link rel="mask-icon" sizes="any" href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/b2bb2fb0ec9c/assets/img/logos/yelp_burst.svg" content="#FF1A1A"><link rel="shortcut icon" href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/dcfe403147fc/assets/img/logos/favicon.ico"><script> window.ga=window.ga||function(){(ga.q=ga.q||[]).push(arguments)};ga.l=+new Date;window.ygaPageStartTime=new Date().getTime();</script><script>\n            window.yelp = window.yelp || {};\

In [87]:
soup = BeautifulSoup(r.text,'html.parser')
regex = re.compile('.*comment.*')
results = soup.find_all('p', {'class' : regex})
reviews = [i.text for i in results]

In [88]:
reviews

['I have been coming to Resonance for facials for about 5 months and I highly recommend! The atmosphere is so relaxing and so aesthetically pleasing. They have their own line of all natural skin care products and I have loved every product I have purchased. 90% of my products are now Inbar+Co.I have been having facials very consistently for the last 20 years and have to say my facials with Amber are by far the best I have had.Everyone at Resonance is so helpful and kind. I have nothing negative to say about this place, highly recommend!',
 "I've been here a handful of times now. I am now wondering if the therapist are certified. Sometimes I've noticed my massages have been choppy and the sheet draping has been sloppy and uneven. The rooms are tiny so if you're a tall person, it may be a bit claustrophobic. There are only hooks to place your belongings, so bring less. I've also never had someone talk almost the entire time I've been massaged. When I get a massage, I want to relax and re

In [79]:
data = pd.DataFrame(np.array(reviews), columns = ['reviews'])

In [80]:
data

reviews
0   I have been coming to Resonance for facials fo...
1   I've been here a handful of times now. I am no...
2   Had my first prenatal massage with Christine. ...
3   I recently went to Mysa day Spa for a 90 "cust...
4                          Hey David! Let me DM you. 
5   I'd rate my experience 100 stars if I could! I...
6   Wonderful deep tissue acupressure 90 min massa...
7   Saw all the good reviews here and decided to g...
8   Great service the facial was wonderful.  Good ...
9   I bet this Spa doesn't provide good service to...
10  Dear Anna,We value your honest feedback and we...
11  Was my first and worst treatment ever!!! Me an...
12  Christine at Mysa is fantastic! I had the myof...
13  The owner reached out to me.  Mistakes happen ...
14  Hi Erica! Hope your day is going well. I direc...
15  This review is solely about the customer servi...

In [81]:
data = data.drop([4,10,14]).reset_index(drop=True)

In [82]:
data

reviews
0   I have been coming to Resonance for facials fo...
1   I've been here a handful of times now. I am no...
2   Had my first prenatal massage with Christine. ...
3   I recently went to Mysa day Spa for a 90 "cust...
4   I'd rate my experience 100 stars if I could! I...
5   Wonderful deep tissue acupressure 90 min massa...
6   Saw all the good reviews here and decided to g...
7   Great service the facial was wonderful.  Good ...
8   I bet this Spa doesn't provide good service to...
9   Was my first and worst treatment ever!!! Me an...
10  Christine at Mysa is fantastic! I had the myof...
11  The owner reached out to me.  Mistakes happen ...
12  This review is solely about the customer servi...

In [83]:
data['sentiment score'] = data['reviews'].apply(lambda x: calc_sentiment_analysis_score(x[:512]))

In [84]:
data

reviews  sentiment score
0   I have been coming to Resonance for facials fo...                5
1   I've been here a handful of times now. I am no...                4
2   Had my first prenatal massage with Christine. ...                3
3   I recently went to Mysa day Spa for a 90 "cust...                1
4   I'd rate my experience 100 stars if I could! I...                5
5   Wonderful deep tissue acupressure 90 min massa...                5
6   Saw all the good reviews here and decided to g...                5
7   Great service the facial was wonderful.  Good ...                4
8   I bet this Spa doesn't provide good service to...                1
9   Was my first and worst treatment ever!!! Me an...                1
10  Christine at Mysa is fantastic! I had the myof...                5
11  The owner reached out to me.  Mistakes happen ...                4
12  This review is solely about the customer servi...                1